In [7]:
#works 
import pandas as pd

df = pd.read_excel('NASDAQ 2010.xlsx')

result_df = pd.DataFrame(columns=['Name1', 'Name2', 'Correlation', 'Edge'])

# Gets unique company names
company_names = df['Name'].unique()

# columns to include in correlation calculation
columns_to_include = ['Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume']

for i in range(len(company_names)):
    for j in range(i + 1, len(company_names)):
        name1 = company_names[i]
        name2 = company_names[j]

        # Extract data for each company and selected columns
        data_name1 = df[df['Name'] == name1][['Date'] + columns_to_include].set_index('Date')
        data_name2 = df[df['Name'] == name2][['Date'] + columns_to_include].set_index('Date')

        #aligns the data by the dates
        merged_data = pd.merge(data_name1, data_name2, left_index=True, right_index=True, suffixes=('_' + name1, '_' + name2))

        # Calculate correlation
        correlation_matrix = merged_data.corr()
        correlation = correlation_matrix.loc['Close_' + name1, 'Close_' + name2]  # Adjust based on the column you want to use

        edge = 'Yes' if correlation > 0.9 else 'No'

        #concatinte
        result_df = pd.concat([result_df, pd.DataFrame({'Name1': [name1], 'Name2': [name2], 'Correlation': [correlation], 'Edge': [edge]})], ignore_index=True)

result_df.to_excel('correlation_results.xlsx', index=False)

In [8]:
import pandas as pd
import igraph as ig
import random
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Read correlation data from the Excel file
df = pd.read_excel('correlation_results.xlsx')

# Create an undirected graph using correlation values as edge weights
#g = ig.Graph.TupleList(df[df['Edge'] == 'Yes'][['Name1', 'Name2', 'Correlation']].itertuples(index=False), directed=False, weights=True)
# Create an undirected graph using correlation values as edge weights
g = ig.Graph.TupleList(
    df[df['Edge'] == 'Yes'][['Name1', 'Name2', 'Correlation']].itertuples(index=False),
    directed=False,
    weights='Correlation'  # Specify the column containing edge weights
)



# Check the attributes of an edge
sample_edge = g.es[0]  # Get the first edge in the graph
print(sample_edge.attributes())

# Remove duplicate edges
g.simplify(multiple=True, loops=True)

# Normalize edge weights for each node
for vertex in g.vs:
    outgoing_edges = g.es.select(_source=vertex.index)
    total_weight = sum(edge.attributes().get('Correlation', 0) for edge in outgoing_edges)
    for edge in outgoing_edges:
        if 'Correlation' in edge.attributes():
            edge['Correlation'] /= total_weight

# Select a random seed set
#seed_set = random.sample(range(g.vcount()), 2)

# Initialize active nodes with the seed set
#active_nodes = set(seed_set)

# Mapping node IDs to letters for visualization
id_to_letter = {i: chr(65 + i) for i in range(g.vcount())}
vertex_labels = [f"{id_to_letter[id]}" for id in range(g.vcount())]

# Layout for visualization
layout = g.layout_fruchterman_reingold() 
fig = make_subplots(rows=1, cols=1)

# Add edges to the plot
for edge in g.get_edgelist():
    x0, y0 = layout[edge[0]]
    x1, y1 = layout[edge[1]]
    fig.add_scatter(x=[x0, x1, None], y=[y0, y1, None], mode='lines', line=dict(color='gray', width=1))

# Add nodes to the plot
fig.add_scatter(x=[coord[0] for coord in layout], y=[coord[1] for coord in layout],
                mode='markers',
                marker=dict(size=10, color=[ "black" for v in range(g.vcount())]),
                text=vertex_labels, showlegend=False)

# Update layout settings
fig.update_layout(
    width=1200, 
    height=800, 
    margin=dict(l=0, r=0, b=0, t=0),
    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
)

# Add annotation for the number of nodes
fig.add_annotation(
    x=0,
    y=0,
    xref="paper",
    yref="paper",
    text=f"Number of Nodes: {g.vcount()}",
    showarrow=False,
    font=dict(size=14),
)

# Show the plot
fig.show()


{'Correlation': 0.9717920047156132}


In [10]:
# Read correlation data from the Excel file
df = pd.read_excel('correlation_results.xlsx')

# Get a list of all unique company names
all_company_names = set(df['Name1'].unique()) | set(df['Name2'].unique())

# Create an empty graph with all nodes
g = ig.Graph.Full(len(all_company_names), directed=False)

# Mapping node IDs to letters for visualization
id_to_letter = {i: chr(65 + i) for i in range(g.vcount())}
vertex_labels = [f"{id_to_letter[id]}" for id in range(g.vcount())]

# Layout for visualization
layout = g.layout_fruchterman_reingold() 
fig = make_subplots(rows=1, cols=1)

# Add nodes to the plot
for coord, label in zip(layout, vertex_labels):
    fig.add_scatter(x=[coord[0]], y=[coord[1]], mode='markers', marker=dict(size=10, color="black"), text=label, showlegend=False)

# Add edges to the plot
for edge in g.get_edgelist():
    x0, y0 = layout[edge[0]]
    x1, y1 = layout[edge[1]]
    fig.add_scatter(x=[x0, x1, None], y=[y0, y1, None], mode='lines', line=dict(color='gray', width=1))

# Update layout settings
fig.update_layout(
    width=1200, 
    height=800, 
    margin=dict(l=0, r=0, b=0, t=0),
    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
)

# Add annotation for the number of nodes
fig.add_annotation(
    x=0,
    y=0,
    xref="paper",
    yref="paper",
    text=f"Number of Nodes: {g.vcount()}",
    showarrow=False,
    font=dict(size=14),
)

# Show the plot
fig.show()


In [10]:



def greedy_ltm2(graph, k):
    seed_set = [] 
    spread = []    
    timelapse = [] 
    start_time = time.time()  

    print("Starting greedy_ltm function")  # Debugging info

    for i in range(k):
        print(f"Iteration {i + 1}:")
        best_spread = 0
        best_nodes = None
        
        for j in set(range(graph.vcount())) - set(seed_set):
            for l in set(range(graph.vcount())) - set(seed_set):
                if l != j:  # Ensure the two nodes are distinct
                    current_seed_set = seed_set + [j, l]
                    current_spread, _ = ltm(graph, current_seed_set)

                    if current_spread is not None and current_spread > best_spread:
                        best_spread = current_spread
                        best_nodes = (j, l)

        if best_nodes is not None:
            seed_set.extend(best_nodes)
            spread.append(best_spread)
            timelapse.append(time.time() - start_time)
            print("Current seed set:", seed_set)
            print("Best nodes:", best_nodes)
        else:
            print("No suitable nodes found, stopping iteration.")
            break

    print("Reached end of loop")  # Debugging info    
    return seed_set, spread, timelapse  # Return final seed set, spread, and time



# Parameters for greedy_ltm function
k = 3  # Number of nodes to select as seed set

# Call the function
seed_set, spread, timelapse = greedy_ltm2(g, k)

_, activated_nodes = ltm(g, seed_set)


# Mapping node IDs to letters for visualization
id_to_letter = {i: chr(65 + i) for i in range(g.vcount())}
vertex_labels = [f"{id_to_letter[id]}" for id in range(g.vcount())]

# Layout for visualization
layout = g.layout_fruchterman_reingold() 
fig = make_subplots(rows=1, cols=1)

# Add edges to the plot
for edge in g.get_edgelist():
    x0, y0 = layout[edge[0]]
    x1, y1 = layout[edge[1]]
    fig.add_scatter(x=[x0, x1, None], y=[y0, y1, None], mode='lines', line=dict(color='gray', width=1))

# Add nodes to the plot
fig.add_scatter(x=[coord[0] for coord in layout], y=[coord[1] for coord in layout],
                mode='markers',
                marker=dict(size=10, color=["blue" if v in seed_set else "lightblue" if v in activated_nodes else "black" for v in range(g.vcount())]),
                text=vertex_labels, showlegend=False)


fig.update_layout(
    width=1200, 
    height=800, 
    margin=dict(l=0, r=0, b=0, t=0),
    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
)


fig.add_annotation(
    x=0,
    y=0,
    xref="paper",
    yref="paper",
    text=f"Number of Nodes: {g.vcount()}",
    showarrow=False,
    font=dict(size=14),
)

# Show the plot
fig.show()

print("Final seed set:", seed_set)  # Debugging info


Starting greedy_ltm function
Iteration 1:
Current seed set: [54, 60]
Best nodes: (54, 60)
Iteration 2:
Current seed set: [54, 60, 37, 41]
Best nodes: (37, 41)
Iteration 3:
Current seed set: [54, 60, 37, 41, 28, 35]
Best nodes: (28, 35)
Reached end of loop


Final seed set: [54, 60, 37, 41, 28, 35]
